## Using the EWXPWSDB Collector Class

# <span style="color:red">clear all output before saving: db output contains passwords! </span>

### Overview 
this walks through process of

- creating a temporary DB
- using the collector class for existing station records to
    - get past data 
    - pull data for short period, e.g. from a scheduler
    - get all recent data, aka catch up data from last record


### Requirements

- Postgresql database available and has an example database in it (local or remote)
- the URL for that database is in `../.env` or in the environment
- example data file [../data/test_stations.tsv](../data/test_stations.tsv)



In [1]:
%load_ext autoreload
%autoreload 2

## Constants/Config

In [2]:

station_file = '../data/test_stations.tsv'
station_type = 'ZENTRA'
station_code = 'TESTMETERFO'	

In [3]:

from ewxpwsdb.db.database import Session, init_db, get_db_url, get_engine
from ewxpwsdb.db.models import WeatherStation, Reading, StationType, APIResponse
from ewxpwsdb.db.importdata import import_station_file
from ewxpwsdb.collector import Collector
from ewxpwsdb.time_intervals import UTCInterval
from sqlmodel import select

2025-06-17 10:42:08,223 [INFO] ewxpwsdb: Package initialized
2025-06-17 10:42:08,483 [INFO] ewxpwsdb.weather_apis: API and Config class types initialized.


## create engine temp database

In [4]:
from ewxpwsdb.db.database import create_temp_pg_engine, get_db_url, init_db, Session
from ewxpwsdb.db.models import WeatherStation # , Reading, StationType, APIResponse

engine = create_temp_pg_engine(get_db_url(), name_prefix = 'notebook_testing')

temp_db_url = engine.url
print(engine)
print(temp_db_url.database)
init_db(engine,station_file)

2025-06-17 10:42:11,723 [INFO] ewxpwsdb.db.importdata: Station with type 'DAVIS' merged into the database
2025-06-17 10:42:11,725 [INFO] ewxpwsdb.db.importdata: Station with type 'LOCOMOS' merged into the database
2025-06-17 10:42:11,726 [INFO] ewxpwsdb.db.importdata: Station with type 'ONSET' merged into the database
2025-06-17 10:42:11,728 [INFO] ewxpwsdb.db.importdata: Station with type 'RAINWISE' merged into the database
2025-06-17 10:42:11,730 [INFO] ewxpwsdb.db.importdata: Station with type 'SPECTRUM' merged into the database
2025-06-17 10:42:11,731 [INFO] ewxpwsdb.db.importdata: Station with type 'ZENTRA' merged into the database


Engine(postgresql+psycopg2://localhost:5432/notebook_testing_upfzstvmpw)
notebook_testing_upfzstvmpw


In [5]:
def get_one_station(station_type, station_code = None, engine=engine):
    """ global engine is default"""

    if station_code:
        statement = select(WeatherStation).where(WeatherStation.station_code == station_code)
    else:
        statement = select(WeatherStation).where(WeatherStation.station_type == station_type)

    with Session(engine) as session:
        results = session.exec(statement)
        weather_station = results.first()

    return weather_station

In [6]:
statement = select(WeatherStation).where(WeatherStation.station_type == station_type)
with Session(engine) as session:
    results = session.exec(statement)
    weather_station = results.first()
    
weather_station

WeatherStation(station_code='EWX-METER-FO2', id=5, lat=42.70733, location_description='EWX Field Office', active=True, timezone='US/Eastern', station_type='ZENTRA', install_date=datetime.date(2023, 9, 10), ewx_user_id='0', lon=-84.46507, background_place='MSU', api_config='{"sn":"z6-20553","token":"12cc21d9f697e478885cca9b65307d27872dfb18"}')

In [14]:
station = get_one_station(station_type=station_type, station_code = 'EWX-METER-FO', engine=engine)
station



WeatherStation(station_code='EWX-METER-FO', id=6, lat=42.70733, location_description='EWX Field Office', active=True, timezone='US/Eastern', station_type='ZENTRA', install_date=datetime.date(2023, 5, 1), ewx_user_id='0', lon=-84.46507, background_place='MSU', api_config='{"sn":"z6-12564","token":"5b8f637a718b9e3ad6e31eec81f0b51d91ac38bd"}')

In [15]:
collector = Collector(station, engine)
collector.weather_api

2025-06-17 10:45:17,195 [INFO] ewxpwsdb.collector: Initializing collector for station id 6
2025-06-17 10:45:17,197 [INFO] ewxpwsdb.weather_apis.zentra_api: Initialized ZentraAPI for station EWX-METER-FO


In [ ]:
zentra = collector.weather_api

In [21]:

from datetime import timedelta
from ewxpwsdb.time_intervals import previous_fourteen_minute_interval
interval = previous_fourteen_minute_interval()

readings = zentra.get_readings(start_datetime=interval.start, end_datetime = interval.end)
readings

2025-06-17 10:50:19,957 [DEBUG] urllib3.connectionpool: Starting new HTTPS connection (1): zentracloud.com:443


2025-06-17 10:50:25,315 [DEBUG] urllib3.connectionpool: https://zentracloud.com:443 "GET /api/v4/get_readings/?device_sn=z6-12564&start_date=2025-06-17+10%3A16%3A00&end_date=2025-06-17+10%3A30%3A00&per_page=2000&page_num=1 HTTP/1.1" 200 None
2025-06-17 10:50:25,359 [INFO] ewxpwsdb.weather_apis.zentra_api: Successfully retrieved data for interval 2025-06-17 14:16:00+00:00 - 2025-06-17 14:30:00+00:00


[APIResponse(request_id='293c8dae-bcb7-4399-b1c0-16704067edfa', weatherstation_id=6, request_datetime=datetime.datetime(2025, 6, 17, 14, 50, 19, 956083, tzinfo=datetime.timezone.utc), data_start_datetime=datetime.datetime(2025, 6, 17, 14, 16, tzinfo=datetime.timezone.utc), data_end_datetime=datetime.datetime(2025, 6, 17, 14, 30, tzinfo=datetime.timezone.utc), package_version='0.1', station_sampling_interval=5, request_url='https://zentracloud.com/api/v4/get_readings/?device_sn=z6-12564&start_date=2025-06-17+10%3A16%3A00&end_date=2025-06-17+10%3A30%3A00&per_page=2000&page_num=1', response_status_code=200, response_reason='OK', response_text='{"pagination": {"per_page": 2000, "page_num": 1, "next_url": "https://zentracloud.com/api/v4/get_readings/?device_sn=z6-12564&start_date=2025-06-17+10%3A16%3A00&end_date=2025-06-17+10%3A30%3A00&per_page=2000&page_num=2", "max_mrid": 429208, "page_num_readings": 3, "page_num_outputs": 72, "page_start_date": "2025-06-17 10:20:00-04:00", "page_end_date

In [ ]:
zentra.data_present_in_response(readings[0])


True

In [28]:
import json
api_response_record = readings[0]
response_data_str = api_response_record.response_text
response_data  = json.loads(response_data_str)
response_data.keys()

dict_keys(['pagination', 'data'])

In [31]:
readings_by_timestamp = {}
for sensor in response_data.get('data'):
    print(sensor)
    print(sensor in zentra._sensor_fieldnames)
    
sensors = response_data.get('data')

Air Temperature
True
Atmospheric Pressure
False
Battery Percent
False
Battery Voltage
False
Gust Speed
True
Leaf Wetness
False
Leaf Wetness (high)
False
Lightning Activity
False
Lightning Distance
False
Logger Temperature
False
Max Precip Rate
False
Precipitation
True
RH Sensor Temp
False
Reference Pressure
False
Relative Humidity
True
Soil Temperature
True
Solar Radiation
True
VPD
False
Water Content
False
Wetness Level
True
Wind Direction
True
Wind Speed
True
X-axis Level
False
Y-axis Level
False


In [ ]:
readings_by_timestamp = {}

from datetime import datetime, timezone
for sensor in response_data.get('data'):   
    if sensor not in zentra._sensor_fieldnames:
        continue            
    for sensor_data in response_data['data'][sensor]:
        sensor_units = sensor_data['metadata']['units'] 
        ewx_field_name, this_sensor_transform = zentra._lookup_sensor_transform(sensor, sensor_units)
        print(ewx_field_name, this_sensor_transform)
        
        for zentra_reading in sensor_data['readings']:                    
            timestamp = zentra_reading['timestamp_utc']
            print(timestamp)
        #     # if we haven't seen this timestamp before, create a new entry in our readings dict
            if timestamp not in readings_by_timestamp:
        #         # add the datetime which would be the same for all readings with this time stamp
                 reading_datetime = datetime.fromtimestamp(timestamp).astimezone(timezone.utc)
                 readings_by_timestamp[timestamp] = {'data_datetime': reading_datetime}

            readings_by_timestamp[timestamp][ewx_field_name] = this_sensor_transform(zentra_reading['value'])
            print(readings_by_timestamp)

        
    


atmp <bound method WeatherAPI.f_to_c of <ewxpwsdb.weather_apis.zentra_api.ZentraAPI object at 0x134287310>>
1750170600
1750170300
1750170000
wspd_max <bound method WeatherAPI.mph_to_ms of <ewxpwsdb.weather_apis.zentra_api.ZentraAPI object at 0x134287310>>
1750170600
1750170300
1750170000
pcpn <bound method WeatherAPI.in_to_mm of <ewxpwsdb.weather_apis.zentra_api.ZentraAPI object at 0x134287310>>
1750170600
1750170300
1750170000
relh <bound method WeatherAPI.identity of <ewxpwsdb.weather_apis.zentra_api.ZentraAPI object at 0x134287310>>
1750170600
1750170300
1750170000
stmp <bound method WeatherAPI.f_to_c of <ewxpwsdb.weather_apis.zentra_api.ZentraAPI object at 0x134287310>>
1750170600
1750170300
1750170000
srad <bound method WeatherAPI.identity of <ewxpwsdb.weather_apis.zentra_api.ZentraAPI object at 0x134287310>>
1750170600
1750170300
1750170000
lws <bound method ZentraAPI._zentra_leaf_wetness_transform of <ewxpwsdb.weather_apis.zentra_api.ZentraAPI object at 0x134287310>>
1750170600


In [9]:
collector._session.commit()

In [10]:
from datetime import timedelta
from ewxpwsdb.time_intervals import UTCInterval
duration_min = 70
viable_interval = UTCInterval.previous_interval(delta_mins=duration_min)
yesterday = UTCInterval(start=viable_interval.start - timedelta(days = 1), 
                           end = viable_interval.end - timedelta(days = 1)
                           )
yesterday

UTCInterval(start=datetime.datetime(2025, 6, 16, 13, 20, tzinfo=datetime.timezone.utc), end=datetime.datetime(2025, 6, 16, 14, 30, tzinfo=datetime.timezone.utc))

In [11]:
from datetime import timedelta
from ewxpwsdb.time_intervals import previous_fourteen_minute_interval

interval = previous_fourteen_minute_interval()

interval.start = interval.start - timedelta(hours = 1)
interval.end = interval.end - timedelta(hours = 0.5)
interval

UTCInterval(start=datetime.datetime(2025, 6, 17, 13, 16, tzinfo=datetime.timezone.utc), end=datetime.datetime(2025, 6, 17, 14, 0, tzinfo=datetime.timezone.utc))

In [12]:
today_interval = UTCInterval.one_day_interval()  # this defaults to getting the time range from midnight to now
two_day_interval = UTCInterval(start = (today_interval.start - timedelta(days = 1)), end = today_interval.end)
two_day_interval

UTCInterval(start=datetime.datetime(2025, 6, 16, 0, 0, tzinfo=datetime.timezone.utc), end=datetime.datetime(2025, 6, 17, 14, 30, tzinfo=datetime.timezone.utc))

In [13]:
from datetime import datetime, timezone
today_utc = datetime.now(timezone.utc).date()

collector.request_and_store_weather_data_utc(UTCInterval.one_day_interval(d = today_utc- timedelta(days = 1)))

2025-06-17 10:42:46,174 [INFO] ewxpwsdb.collector: Requesting and storing weather data for station 5 from 2025-06-16 00:00:00+00:00 to 2025-06-16 23:59:00+00:00
2025-06-17 10:42:46,179 [DEBUG] urllib3.connectionpool: Starting new HTTPS connection (1): zentracloud.com:443
2025-06-17 10:42:49,214 [DEBUG] urllib3.connectionpool: https://zentracloud.com:443 "GET /api/v4/get_readings/?device_sn=z6-20553&start_date=2025-06-15+20%3A00%3A00&end_date=2025-06-16+19%3A59%3A00&per_page=2000&page_num=1 HTTP/1.1" 200 None
2025-06-17 10:42:49,643 [INFO] ewxpwsdb.weather_apis.zentra_api: Successfully retrieved data for interval 2025-06-16 00:00:00+00:00 - 2025-06-16 23:59:00+00:00
2025-06-17 10:42:49,718 [INFO] ewxpwsdb.collector: Saving readings from API responses for station 5
2025-06-17 10:42:49,726 [DEBUG] ewxpwsdb.weather_apis.weather_api: Transformed readings: []
2025-06-17 10:42:49,727 [ERROR] ewxpwsdb.collector: No reading data extracted from responses for station 5


RuntimeError: no reading data extracted from responses [APIResponse(weatherstation_id=5, response_text='{"pagination": {"per_page": 2000, "page_num": 1, "next_url": "https://zentracloud.com/api/v4/get_readings/?device_sn=z6-20553&start_date=2025-06-15+20%3A00%3A00&end_date=2025-06-16+19%3A59%3A00&per_page=2000&page_num=2", "max_mrid": 233809, "page_num_readings": 288, "page_num_outputs": 6912, "page_start_date": "2025-06-15 20:00:00-04:00", "page_end_date": "2025-06-16 19:55:00-04:00", "page_start_mrid": 233347, "page_end_mrid": 233634}, "data": {"Air Temperature": [{"metadata": {"device_sn": "z6-20553", "device_name": "envwx-meter-fo2", "port_number": 1, "sensor_sn": "ATM-410008286", "sensor_name": "ATMOS 41", "units": " \\u00b0F", "errors": []}, "readings": [{"timestamp_utc": 1750118100, "datetime": "2025-06-16 19:55:00-04:00", "tz_offset": -14400, "value": 80.0, "precision": 1, "mrid": 233634, "error_flag": false, "error_description": null}, {"timestamp_utc": 1750117800, "datetime":

In [ ]:
collector.get_readings(1)

In [ ]:
# call the method to see if it's working
somerex = collector.request_and_store_weather_data_utc(interval)
somerex

In [ ]:
# are api response ids being saved in the object?

collector.current_api_response_record_ids

In [ ]:
# to re-fill this sqlalchemy record cache, just ask for some piece of the data
print(collector.current_api_response.id)
# now the object cache is refilled and should be present
collector.current_api_response

In [ ]:
# show the transformed readings, if any
collector.current_readings

In [ ]:
# again, demonstrate that the readings were stored in the database by checking the ID field
collector.current_readings[0].id


## Test/Demo getting a full day of readings

In [ ]:
viable_interval = UTCInterval.previous_fifteen_minutes()
collector.request_and_store_weather_data_utc(viable_interval)


In [ ]:
yesterday = UTCInterval(start=viable_interval.start - timedelta(days = 1),
                             end = viable_interval.end - timedelta(days = 1)
                               )
print(yesterday)
collector._session.rollback()

response_ids = collector.request_and_store_weather_data_utc(yesterday)
print("response ids:")
print(response_ids)
print("reading ids:")
print(collector.current_reading_ids)

In [ ]:
## there _should_ be readings from the same interval in there now     

readings = collector.get_readings_by_date(yesterday)

In [ ]:
print(readings)

## Test/demo of restricting data inserts

This used to throw an exception when saving readings with the same timestamp and station. 
however, even though this is a unique constraint on these columns, the collector code checks for that, and simply 
updates the record.  This is known as an 'upsert' but it doesn't using the Postgresql + SQLAlchemy upsert but rather some custom code. 

In [ ]:

from sqlalchemy.exc import IntegrityError

try:
    something = collector.save_readings_from_responses(api_responses = collector.current_api_response)
except IntegrityError as e:
    collector._session.rollback()
    print("integrity error prevented duplicate records from being inserted")

# what happens to the current readings? 
collector.current_readings

In [ ]:
# ensure the rollback worked

try:
    something = collector.save_readings_from_responses(api_responses = collector.current_api_response)
except IntegrityError as e:
    collector._session.rollback()
    print("didn't get the rollback error")

    

In [ ]:
# do we still have radings after a rollback?
readings = collector.get_readings(n=5)
readings


## Test of Backfill process

this will look for gaps and fill them 

start with some disconnected time intervals

In [ ]:
# start by adding data to create gaps.  This assumes the station has been online for a while

few_days_ago = UTCInterval(start = yesterday.start - timedelta(days = 3), end = yesterday.end - timedelta(days = 3))
print(few_days_ago)
more_days_ago = UTCInterval(start = few_days_ago.start - timedelta(days = 2), end = few_days_ago.end - timedelta(days = 2))
print(more_days_ago)

In [ ]:
print(f"getting data for interval: {more_days_ago}")
print(collector.request_and_store_weather_data_utc(more_days_ago))
print("requests")

print(f"getting data for interval: {few_days_ago}")
print(collector.request_and_store_weather_data_utc(few_days_ago))
print("requests")




*now try to get a backfill*

In [ ]:
from datetime import UTC

days_from_now = (datetime.now(UTC) - more_days_ago.start).days

print(f"initiating backfill for {days_from_now} days")
readings_added = collector.backfill(n_days_prior=days_from_now)

print(f"{len(readings_added)} readings added")
print(f"first reading element = {readings_added[0]}")





double checking on how a collector needs to get records:  the time interval must not have start = end


In [ ]:
from ewxpwsdb.station_readings import StationReadings
station_readings = StationReadings(collector.station, engine=engine)


In [ ]:
known_interval = UTCInterval(start=datetime(2024, 6, 27, 0, 0, tzinfo=timezone.utc), end=datetime(2024, 6, 27, 20, 0, tzinfo=timezone.utc))
empty_interval = UTCInterval(start=datetime(2024, 6, 27, 15, 0, tzinfo=timezone.utc), end=datetime(2024, 6, 27, 15, 0, tzinfo=timezone.utc))
print(station_readings.readings_by_interval_utc(known_interval))
empty_interval.end = empty_interval.end + timedelta(minutes = 5)
x = collector.request_and_store_weather_data_utc(empty_interval)
print(x)

### Clean up

remove test database

In [ ]:

from ewxpwsdb.db.database import drop_pg_db, list_pg_databases
from sqlalchemy.orm import close_all_sessions

if collector:
    collector._session.close()
    collector._engine.dispose()

close_all_sessions()




print(f"attempting to drop db {engine.url.database}")
result = drop_pg_db(engine.url.database, get_db_url())
    # engine)
print(result)
engine.dispose()

